In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from collections import Counter

In [2]:
# Изменить настройку - показывать все колонки не скрывая.
pd.set_option('display.max_columns', None)

In [3]:
data = pd.read_csv('movie_bd_v5.csv')
data.sample(5)

imdb_id     budget    revenue          original_title  \
1445  tt0477347  110000000  574480841     Night at the Museum   
326   tt1179891   15000000  100734718     My Bloody Valentine   
1085  tt0242653  150000000  424988211  The Matrix Revolutions   
1561  tt0378194   30000000  152159461       Kill Bill: Vol. 2   
1779  tt0446013   45000000   30822861              Pathfinder   

                                                   cast  \
1445  Ben Stiller|Jake Cherry|Carla Gugino|Robin Wil...   
326   Jensen Ackles|Jaime King|Kerr Smith|Betsy Rue|...   
1085  Keanu Reeves|Laurence Fishburne|Carrie-Anne Mo...   
1561  Uma Thurman|David Carradine|Daryl Hannah|Micha...   
1779  Karl Urban|Moon Bloodgood|Russell Means|Clancy...   

                            director  \
1445                      Shawn Levy   
326                  Patrick Lussier   
1085  Lilly Wachowski|Lana Wachowski   
1561               Quentin Tarantino   
1779                   Marcus Nispel   

                                               tagline  \
1445                       Where History Comes To Life   
326                       He's gonna break your heart.   
1085       Everything that has a beginning has an end.   
1561              The bride is back for the final cut.   
1779  Two Worlds, One War. The Ultimate Battle Begins.   

                                               overview  runtime  \
1445  Chaos reigns at the natural history museum whe...      108   
326   Ten years ago, a tragedy changed the town of H...      101   
1085  The human city of Zion defends itself against ...      129   
1561  The Bride unwaveringly continues on her roarin...      136   
1779  A Viking boy is left behind after his clan bat...       99   

                                         genres  \
1445     Action|Adventure|Comedy|Family|Fantasy   
326                              Mystery|Horror   
1085  Adventure|Action|Thriller|Science Fiction   
1561                      Action|Crime|Thriller   
1779                                     Action   

                                   production_companies release_date  \
1445  Ingenious Film Partners|Twentieth Century Fox ...   10/20/2006   
326                                           Lionsgate    1/16/2009   
1085  Village Roadshow Pictures|NPV Entertainment|Si...    11/5/2003   
1561       Miramax Films|A Band Apart|Super Cool ManChu    4/16/2004   
1779  Twentieth Century Fox Film Corporation|Dune En...    1/11/2007   

      vote_average  release_year  
1445           6.2          2006  
326            5.3          2009  
1085           6.4          2003  
1561           7.5          2004  
1779           5.4          2007

In [4]:
data.describe()

budget       revenue      runtime  vote_average  release_year
count  1.889000e+03  1.889000e+03  1889.000000   1889.000000   1889.000000
mean   5.431083e+07  1.553653e+08   109.658549      6.140762   2007.860773
std    4.858721e+07  2.146698e+08    18.017041      0.764763      4.468841
min    5.000000e+06  2.033165e+06    63.000000      3.300000   2000.000000
25%    2.000000e+07  3.456058e+07    97.000000      5.600000   2004.000000
50%    3.800000e+07  8.361541e+07   107.000000      6.100000   2008.000000
75%    7.200000e+07  1.782626e+08   120.000000      6.600000   2012.000000
max    3.800000e+08  2.781506e+09   214.000000      8.100000   2015.000000

# Изучение и проверка форматов датасета

Этого не было в задании, но мне кажется - разумная предосторожность.

Поскольку в реальной жизни не факт что датасет содержит отчищенные данные... сначала я хочу проверить что датасет - чищенный и формат достаточно хороший и достаточно предсказуемый.

И самым первым делом - ответить на вопрос - какая форма этого датасета?:

In [5]:
data.shape

(1889, 14)

1889 строк, 14 столбцов

### 1. Есть ли пустые значения в этом датасете (NaN, None, NaT)?

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1889 entries, 0 to 1888
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   imdb_id               1889 non-null   object 
 1   budget                1889 non-null   int64  
 2   revenue               1889 non-null   int64  
 3   original_title        1889 non-null   object 
 4   cast                  1889 non-null   object 
 5   director              1889 non-null   object 
 6   tagline               1889 non-null   object 
 7   overview              1889 non-null   object 
 8   runtime               1889 non-null   int64  
 9   genres                1889 non-null   object 
 10  production_companies  1889 non-null   object 
 11  release_date          1889 non-null   object 
 12  vote_average          1889 non-null   float64
 13  release_year          1889 non-null   int64  
dtypes: float64(1), int64(4), object(9)
memory usage: 206.7+ KB


\- так, судя по 1889 non-null во всех колонках, пустых значений (NaN, Null, NaT) нет. Отлично.

### 2. Есть ли отклонения от формата в колонке imdb_id?

(любые id в таблицах всегда важные потому что они указывают на уникальные значения)

Проверяю что все значения в imdb состоят только из двух латинских букв "t" в начале id после которых - одна цифра или более цифр... при этом в начале и в конце строки не должно быть пробелов...

In [7]:
data[~data.imdb_id.str.match(r'^tt\d+$')]

Empty DataFrame
Columns: [imdb_id, budget, revenue, original_title, cast, director, tagline, overview, runtime, genres, production_companies, release_date, vote_average, release_year]
Index: []

\- ок, строк с плохим форматом не найдено. Отлично.

Так, а работает ли наше регулярное выражение?

In [8]:
len(data[data.imdb_id.str.match(r'^tt\d+$')])

1889

\- найдено 1889 строк с этим форматом, значит работает. Отлично.

### 3. Есть ли дубликаты в колонке imdb_id?

In [9]:
len(data.imdb_id.unique())

1889

1889 - все уникальные. Отлично.

### 4. В каком формате release_date?

In [10]:
data.release_date.str.match(r'^[\d]{1,2}[/][\d]{1,2}[/][\d]{4}').unique()

array([ True])

\- нет значений False - значит все - в ожидаемом формате... Посмотрим что тут день а что - месяц:

In [11]:
data.release_date.str.extract(r'^(\d{1,2})/(\d{1,2})/(\d{4})')

0   1     2
0      6   9  2015
1      5  13  2015
2      3  18  2015
3     12  15  2015
4      4   1  2015
...   ..  ..   ...
1884   7  13  2000
1885  10  27  2000
1886   6  30  2000
1887   2  16  2000
1888   7  19  2000

[1889 rows x 3 columns]

In [12]:
data.release_date.str.extract(r'^(\d{1,2})/(\d{1,2})/(\d{4})').describe()

0     1     2
count   1889  1889  1889
unique    12    31    16
top        9    25  2011
freq     227    85   143

In [13]:
data.release_date.str.extract(r'^(\d{1,2})/(\d{1,2})/(\d{4})').astype(int).describe()

0            1            2
count  1889.000000  1889.000000  1889.000000
mean      6.933298    15.432504  2007.860773
std       3.390196     8.446355     4.468841
min       1.000000     1.000000  2000.000000
25%       4.000000     8.000000  2004.000000
50%       7.000000    15.000000  2008.000000
75%      10.000000    22.000000  2012.000000
max      12.000000    31.000000  2015.000000

Угу - первая позиция - месяц \[1; 12\], вторая - число \[1; 31\], третья - год \[2000; 2004\]. Отлично.

### Итог

Ок, датасет мне нравится.

# Предобработка

In [14]:
answers = {} # создадим словарь для ответов

# Тут другие ваши предобработки колонок:

def convert_pipe_string_to_set(genres):
    """Преобразует строку с "|" в множество
    
    Именованные аргументы:
    genres - - строка в формате "Spam|Viking|Pidgeon"
    
    На выходе - множество строк (set of strings).
    
    Зачем эта функция:
    ==================
    Многие поля в датасете задаются как "Spam|Viking|Pidgeon".
    Мне кажется что с ними удобней работать если привести их к типу set
    (множество).
    
    У каждого элемента множества, эта функция дополнительно отрезает
    пустые символы в начале и в конце строке - мне кажется это сделает
    работу с датасетом более удобной и предсказуемой.
    """
    
    if type(genres) != str:
        genres = ''
    
    genre_list = [str(x).strip() for x in genres.split('|')]
    return set(genre_list)


# Выделить поле с названием как в вариантах ответов.
data['neat_title'] = data.apply(
    lambda x: f'{x.original_title} ({x.imdb_id})', axis=1
)

# Начать хранить Прибыль (Прибыль = Сборы - Бюджет).
data['profit'] = data.apply(lambda x: x.revenue - x.budget, axis=1)

# Начать хранить жанры фильма как множество.
data['genre_set'] = (
    data
    .genres
    .apply(convert_pipe_string_to_set)
)

# Начать хранить режиссёров фильма как множество.
data['director_set'] = (
    data
    .director
    .apply(convert_pipe_string_to_set)
)

# Начать хранить актёров фильма как множество.
data['cast_set'] = (
    data
    .cast
    .apply(convert_pipe_string_to_set)
)

# Начать хранить актёров фильма как множество.
data['company_set'] = (
    data
    .production_companies
    .apply(convert_pipe_string_to_set)
)

# Преобразовать дату из str в datetime.
data['release_date'] = pd.to_datetime(
    data.release_date, format='%m/%d/%Y'
)

# Начать хранить месяц как отдельное поле.
data['release_month'] = data.release_date.apply(lambda x: x.month)

data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1889 entries, 0 to 1888
Data columns (total 21 columns):
 #   Column                Non-Null Count  Dtype         
---  ------                --------------  -----         
 0   imdb_id               1889 non-null   object        
 1   budget                1889 non-null   int64         
 2   revenue               1889 non-null   int64         
 3   original_title        1889 non-null   object        
 4   cast                  1889 non-null   object        
 5   director              1889 non-null   object        
 6   tagline               1889 non-null   object        
 7   overview              1889 non-null   object        
 8   runtime               1889 non-null   int64         
 9   genres                1889 non-null   object        
 10  production_companies  1889 non-null   object        
 11  release_date          1889 non-null   datetime64[ns]
 12  vote_average          1889 non-null   float64       
 13  release_year      

In [15]:
display(data.describe())

budget       revenue      runtime  vote_average  release_year  \
count  1.889000e+03  1.889000e+03  1889.000000   1889.000000   1889.000000   
mean   5.431083e+07  1.553653e+08   109.658549      6.140762   2007.860773   
std    4.858721e+07  2.146698e+08    18.017041      0.764763      4.468841   
min    5.000000e+06  2.033165e+06    63.000000      3.300000   2000.000000   
25%    2.000000e+07  3.456058e+07    97.000000      5.600000   2004.000000   
50%    3.800000e+07  8.361541e+07   107.000000      6.100000   2008.000000   
75%    7.200000e+07  1.782626e+08   120.000000      6.600000   2012.000000   
max    3.800000e+08  2.781506e+09   214.000000      8.100000   2015.000000   

             profit  release_month  
count  1.889000e+03    1889.000000  
mean   1.010545e+08       6.933298  
std    1.830733e+08       3.390196  
min   -1.657101e+08       1.000000  
25%    5.000000e+06       4.000000  
50%    4.400041e+07       7.000000  
75%    1.201842e+08      10.000000  
max    2.544506e+09      12.000000

In [16]:
display(data)

imdb_id     budget     revenue                        original_title  \
0     tt0369610  150000000  1513528810                        Jurassic World   
1     tt1392190  150000000   378436354                    Mad Max: Fury Road   
2     tt2908446  110000000   295238201                             Insurgent   
3     tt2488496  200000000  2068178225          Star Wars: The Force Awakens   
4     tt2820852  190000000  1506249360                             Furious 7   
...         ...        ...         ...                                   ...   
1884  tt0120903   75000000   157299717                                 X-Men   
1885  tt0192255   22000000    13555988                    The Little Vampire   
1886  tt0131704   76000000    35134820  The Adventures of Rocky & Bullwinkle   
1887  tt0162983   40000000    36037909                            Hanging Up   
1888  tt0163676   15000000     5217498                          The In Crowd   

                                                   cast          director  \
0     Chris Pratt|Bryce Dallas Howard|Irrfan Khan|Vi...   Colin Trevorrow   
1     Tom Hardy|Charlize Theron|Hugh Keays-Byrne|Nic...     George Miller   
2     Shailene Woodley|Theo James|Kate Winslet|Ansel...  Robert Schwentke   
3     Harrison Ford|Mark Hamill|Carrie Fisher|Adam D...       J.J. Abrams   
4     Vin Diesel|Paul Walker|Jason Statham|Michelle ...         James Wan   
...                                                 ...               ...   
1884  Patrick Stewart|Hugh Jackman|Ian McKellen|Hall...      Bryan Singer   
1885  Richard E. Grant|Jonathan Lipnicki|Jim Carter|...          Uli Edel   
1886  Rene Russo|Jason Alexander|Piper Perabo|Randy ...       Des McAnuff   
1887  Meg Ryan|Diane Keaton|Lisa Kudrow|Walter Matth...      Diane Keaton   
1888  Susan Ward|Lori Heuring|Matthew Settle|Nathan ...      Mary Lambert   

                                                tagline  \
0                                     The park is open.   
1                                    What a Lovely Day.   
2                            One Choice Can Destroy You   
3                         Every generation has a story.   
4                                   Vengeance Hits Home   
...                                                 ...   
1884                                   Evolution Begins   
1885  They're not just best friends, they're blood b...   
1886            This summer it's not the same old bull.   
1887                   Every family has a few hang-ups.   
1888                       What would you do to get in?   

                                               overview  runtime  \
0     Twenty-two years after the events of Jurassic ...      124   
1     An apocalyptic story set in the furthest reach...      120   
2     Beatrice Prior must confront her inner demons ...      119   
3     Thirty years after defeating the Galactic Empi...      136   
4     Deckard Shaw seeks revenge against Dominic Tor...      137   
...                                                 ...      ...   
1884  Two mutants, Rogue and Wolverine, come to a pr...      104   
1885  Based on the popular books, the story tells of...       95   
1886  Rocky and Bullwinkle have been living off the ...       88   
1887  A trio of sisters bond over their ambivalence ...       94   
1888  A mentally disturbed young woman takes a job a...      105   

                                         genres  \
0     Action|Adventure|Science Fiction|Thriller   
1     Action|Adventure|Science Fiction|Thriller   
2            Adventure|Science Fiction|Thriller   
3      Action|Adventure|Science Fiction|Fantasy   
4                         Action|Crime|Thriller   
...                                         ...   
1884           Adventure|Action|Science Fiction   
1885                      Horror|Family|Foreign   
1886   Adventure|Animation|Action|Comedy|Family   
1887                               Comedy|Drama   
1888                               

## Мне интересно поизучать уникальные значения некоторых полей которые зацепили глаз

In [17]:
# Показать все уникальные названия компаний в этом датасете.
all_company_names = set()
for x in data.company_set:
    all_company_names |= x

pd.Series(list(all_company_names)).sort_values().to_list()

['"DIA" Productions GmbH & Co. KG',
 '11:11 Mediaworks',
 '1492 Pictures',
 '1984 Private Defense Contractors',
 '2 Entertain',
 '20th Century Fox',
 '20th Century Fox Home Entertainment',
 '21 Laps Entertainment',
 '26 Films',
 '2929 Productions',
 '2S Films',
 '3 Arts Entertainment',
 '3 in the Box',
 '360 Pictures',
 '3Foot7',
 '3L Filmverleih',
 '40 Acres & A Mule Filmworks',
 '4M',
 '5150 Action',
 '80 Days Productions',
 '87Eleven',
 '8:38 Productions',
 '98 MPH Productions',
 'A Band Apart',
 'A Hot Dog',
 'A&E Television Networks',
 'A113',
 'A24',
 'AFG Talons Productions',
 'ANA Media',
 'AR Films',
 'AR-TL',
 'ARD Degeto Film',
 'ARP SÃ©lection',
 'ASAF',
 'AZL Productions KG',
 'Aardman Animations',
 'Abandon Entertainment',
 'Abraham Productions',
 'Achte Babelsberg Film',
 'Ad Hominem Enterprises',
 'Adam Schroeder Productions',
 'Aegis Film Fund',
 'Affirm Films',
 'After Dark Films',
 'Agencja Produkcji Filmowej',
 'Aggregate Films',
 'Ahimsa Films',
 'Akil Production C

In [18]:
# Показать все уникальные имена актёров в этом датасете.
all_cast_names = set()
for x in data.cast_set:
    all_cast_names = all_cast_names | x

pd.Series(list(all_cast_names)).sort_values().to_list()

['50 Cent',
 'A.J. Cook',
 'Aaliyah',
 'Aamir Khan',
 'Aaran Thomas',
 'Aaron Eckhart',
 'Aaron Paul',
 'Aaron Stanford',
 'Aaron Taylor-Johnson',
 'Aaron Wolff',
 'Aaron Yoo',
 'Aasif Mandvi',
 'Abbie Cornish',
 'Abhishek Bachchan',
 'Abigail Bianca',
 'Abigail Breslin',
 'Abigail Hargrove',
 'Adam Alexi-Malle',
 'Adam Arkin',
 'Adam Beach',
 'Adam Brody',
 'Adam Campbell',
 'Adam David Thompson',
 'Adam Driver',
 'Adam G. Sevani',
 'Adam Garcia',
 'Adam Goldberg',
 'Adam Herschman',
 'Adam Lamberg',
 'Adam Levine',
 'Adam Pascal',
 'Adam RodrÃ\xadguez',
 'Adam Sandler',
 'Adam Scott',
 'Addison Timlin',
 'Adelaide Clemens',
 'Adewale Akinnuoye-Agbaje',
 'Adil Hussain',
 'Aditya Roy Kapoor',
 'Adrian Grenier',
 'Adrian Paul',
 'Adriana Barraza',
 'Adrianne Palicki',
 'Adrien Brody',
 'Adrienne Shaw',
 'AdriÃ¡n Alonso Barona',
 'Affion Crockett',
 'Agata Buzek',
 'Agnes Bruckner',
 'Ahmad Khan Mahmoodzada',
 'Ahney Her',
 'Aidan Gillen',
 'Aidan McArdle',
 'Aidan Quinn',
 'Aimee Garcia

In [19]:
# Показать все уникальные названия жанров в этом датасете.
all_genre_names = set()
for x in data.genre_set:
    all_genre_names |= x

pd.Series(list(all_genre_names)).sort_values().to_list()

['Action',
 'Adventure',
 'Animation',
 'Comedy',
 'Crime',
 'Documentary',
 'Drama',
 'Family',
 'Fantasy',
 'Foreign',
 'History',
 'Horror',
 'Music',
 'Mystery',
 'Romance',
 'Science Fiction',
 'Thriller',
 'War',
 'Western']

# 1. У какого фильма из списка самый большой бюджет?

Использовать варианты ответов в коде решения запрещено.    
Вы думаете и в жизни у вас будут варианты ответов?)

In [20]:
# в словарь вставляем номер вопроса и ваш ответ на него
# Пример: 
answers['1'] = '2. Spider-Man 3 (tt0413300)'
# запишите свой вариант ответа
answers['1'] = \
    '5. Pirates of the Caribbean: On Stranger Tides (tt1298650)'
# если ответили верно, можете добавить комментарий со значком "+"

In [21]:
# тут пишем ваш код для решения данного вопроса:
data[data.budget == data.budget.max()]

imdb_id     budget     revenue  \
723  tt1298650  380000000  1021683000   

                                  original_title  \
723  Pirates of the Caribbean: On Stranger Tides   

                                                  cast      director  \
723  Johnny Depp|PenÃ©lope Cruz|Geoffrey Rush|Ian M...  Rob Marshall   

                         tagline  \
723  Live Forever Or Die Trying.   

                                              overview  runtime  \
723  Captain Jack Sparrow crosses paths with a woma...      136   

                       genres  \
723  Adventure|Action|Fantasy   

                                  production_companies release_date  \
723  Walt Disney Pictures|Jerry Bruckheimer Films|M...   2011-05-11   

     vote_average  release_year  \
723           6.3          2011   

                                            neat_title     profit  \
723  Pirates of the Caribbean: On Stranger Tides (t...  641683000   

                        genre_set    director_set  \
723  {Adventure, Fantasy, Action}  {Rob Marshall}   

                                              cast_set  \
723  {Geoffrey Rush, Johnny Depp, Kevin McNally, Pe...   

                                           company_set  release_month  
723  {Jerry Bruckheimer Films, Moving Picture Compa...              5

ВАРИАНТ 2

In [22]:
# можно добавлять разные варианты решения
data[data.budget == data.budget.max()].neat_title.to_list()

['Pirates of the Caribbean: On Stranger Tides (tt1298650)']

# 2. Какой из фильмов самый длительный (в минутах)?

In [23]:
# думаю логику работы с этим словарем вы уже поняли, 
# по этому не буду больше его дублировать
answers['2'] = '2. Gods and Generals (tt0279111)'

In [24]:
data[data.runtime == data.runtime.max()].neat_title.to_list()

['Gods and Generals (tt0279111)']

# 3. Какой из фильмов самый короткий (в минутах)?





In [25]:
answers['3'] = '3. Winnie the Pooh (tt1449283)'

In [26]:
data[data.runtime == data.runtime.min()].neat_title.to_list()

['Winnie the Pooh (tt1449283)']

# 4. Какова средняя длительность фильмов?


In [27]:
answers['4'] = '2. 110'

In [28]:
data.runtime.mean()

109.6585494970884

# 5. Каково медианное значение длительности фильмов? 

In [29]:
answers['5'] = '1. 107'

In [30]:
data.runtime.median()

107.0

# 6. Какой самый прибыльный фильм?
#### Внимание! Здесь и далее под «прибылью» или «убытками» понимается разность между сборами и бюджетом фильма. (прибыль = сборы - бюджет) в нашем датасете это будет (profit = revenue - budget) 

In [31]:
# лучше код получения столбца profit вынести в Предобработку что в начале
answers['6'] = '5. Avatar (tt0499549)'

In [32]:
data[data.profit == data.profit.max()].neat_title.to_list()

['Avatar (tt0499549)']

# 7. Какой фильм самый убыточный? 

In [33]:
answers['7'] = '5. The Lone Ranger (tt1210819)'

In [34]:
data[data.profit == data.profit.min()].neat_title.to_list()

['The Lone Ranger (tt1210819)']

# 8. У скольких фильмов из датасета объем сборов оказался выше бюджета?

In [35]:
answers['8'] = '1. 1478'

In [36]:
len(data[data.profit > 0])

1478

# 9. Какой фильм оказался самым кассовым в 2008 году?

In [37]:
answers['9'] = '4. The Dark Knight (tt0468569)'

In [38]:
data2 = data.query('release_year == 2008')
data2.query('profit == profit.max()').neat_title.to_list()

['The Dark Knight (tt0468569)']

# 10. Самый убыточный фильм за период с 2012 по 2014 г. (включительно)?


In [39]:
answers['10'] = '5. The Lone Ranger (tt1210819)'

In [40]:
data2 = data.query('2012 <= release_year <= 2014')
data2.query('profit == profit.min()').neat_title.to_list()

['The Lone Ranger (tt1210819)']

# 11. Какого жанра фильмов больше всего?

In [41]:
# Эту задачу тоже можно решать разными подходами, попробуй реализовать
# разные варианты если будешь добавлять функцию - выноси ее в
# предобработку что в начале.
answers['11'] = '3. Drama'

In [42]:
# Этот вариант работает успешно только в том случае когда нет
# повторяющихся Жанров внутри одной ячейки.
# Например:
# "Drama|Comedy|Thriller" - вариант будет работать корректно.
# "Drama|Comedy|Drama" - вариант будет давать лживый результат.
Counter(
    data.genres.str.split(r'\|').sum()
).most_common()

[('Drama', 782),
 ('Comedy', 683),
 ('Thriller', 596),
 ('Action', 582),
 ('Adventure', 415),
 ('Crime', 315),
 ('Romance', 308),
 ('Family', 260),
 ('Science Fiction', 248),
 ('Fantasy', 222),
 ('Horror', 176),
 ('Mystery', 168),
 ('Animation', 139),
 ('Music', 64),
 ('History', 62),
 ('War', 58),
 ('Western', 19),
 ('Documentary', 8),
 ('Foreign', 2)]

ВАРИАНТ 2

In [43]:
data2 = pd.DataFrame(
    [{y: 1 for y in x} for x in data.genres.str.split(r'\|')]
).fillna(0)

data2.sum().sort_values(ascending=False)

Drama              782.0
Comedy             683.0
Thriller           596.0
Action             582.0
Adventure          415.0
Crime              315.0
Romance            308.0
Family             260.0
Science Fiction    248.0
Fantasy            222.0
Horror             176.0
Mystery            168.0
Animation          139.0
Music               64.0
History             62.0
War                 58.0
Western             19.0
Documentary          8.0
Foreign              2.0
dtype: float64

ВАРИАНТ 3

In [44]:
data2 = pd.DataFrame(
    dict(
        data.genres.str.split(r'\|').apply(lambda x: Counter(x))
    )
).fillna(0).transpose()

data2.sum().sort_values(ascending=False)

Drama              782.0
Comedy             683.0
Thriller           596.0
Action             582.0
Adventure          415.0
Crime              315.0
Romance            308.0
Family             260.0
Science Fiction    248.0
Fantasy            222.0
Horror             176.0
Mystery            168.0
Animation          139.0
Music               64.0
History             62.0
War                 58.0
Western             19.0
Documentary          8.0
Foreign              2.0
dtype: float64

ВАРИАНТ 4

In [45]:
(
    data
    .genres
    .fillna('')
    .apply(str)
    .str
    .split('\|')
    .apply(np.unique)
    .apply(Counter)
    .sum()
    .most_common()
)

[('Drama', 782),
 ('Comedy', 683),
 ('Thriller', 596),
 ('Action', 582),
 ('Adventure', 415),
 ('Crime', 315),
 ('Romance', 308),
 ('Family', 260),
 ('Science Fiction', 248),
 ('Fantasy', 222),
 ('Horror', 176),
 ('Mystery', 168),
 ('Animation', 139),
 ('Music', 64),
 ('History', 62),
 ('War', 58),
 ('Western', 19),
 ('Documentary', 8),
 ('Foreign', 2)]

ВАРИАНТ 5

In [46]:
(
    data
    .genre_set
    .apply(Counter)
    .sum()
    .most_common()
)

[('Drama', 782),
 ('Comedy', 683),
 ('Thriller', 596),
 ('Action', 582),
 ('Adventure', 415),
 ('Crime', 315),
 ('Romance', 308),
 ('Family', 260),
 ('Science Fiction', 248),
 ('Fantasy', 222),
 ('Horror', 176),
 ('Mystery', 168),
 ('Animation', 139),
 ('Music', 64),
 ('History', 62),
 ('War', 58),
 ('Western', 19),
 ('Documentary', 8),
 ('Foreign', 2)]

# 12. Фильмы какого жанра чаще всего становятся прибыльными? 

In [47]:
answers['12'] = '1. Drama'

In [48]:
(
    data[data.profit > 0]
    .genres
    .fillna('')
    .apply(str)
    .str
    .split('\|')
    .apply(np.unique)
    .apply(Counter)
    .sum()
    .most_common()
)

[('Drama', 560),
 ('Comedy', 551),
 ('Thriller', 446),
 ('Action', 444),
 ('Adventure', 337),
 ('Romance', 242),
 ('Crime', 231),
 ('Family', 226),
 ('Science Fiction', 195),
 ('Fantasy', 188),
 ('Horror', 150),
 ('Animation', 120),
 ('Mystery', 119),
 ('Music', 47),
 ('History', 46),
 ('War', 41),
 ('Western', 12),
 ('Documentary', 7)]

ВАРИАНТ 2

In [49]:
(
    data[data.profit > 0]
    .genre_set
    .apply(Counter)
    .sum()
    .most_common()
)

[('Drama', 560),
 ('Comedy', 551),
 ('Thriller', 446),
 ('Action', 444),
 ('Adventure', 337),
 ('Romance', 242),
 ('Crime', 231),
 ('Family', 226),
 ('Science Fiction', 195),
 ('Fantasy', 188),
 ('Horror', 150),
 ('Animation', 120),
 ('Mystery', 119),
 ('Music', 47),
 ('History', 46),
 ('War', 41),
 ('Western', 12),
 ('Documentary', 7)]

# 13. У какого режиссера самые большие суммарные кассовые сборы?

In [50]:
answers['13'] = '5. Peter Jackson'

In [51]:
(
    data[['director_set', 'profit']]
    .apply(
        lambda x: Counter({name: x.profit for name in x.director_set }),
        axis='columns'
    )
    .sum()
    .most_common()
)

[('Peter Jackson', 5202593685),
 ('David Yates', 3379295625),
 ('Christopher Nolan', 3162548502),
 ('J.J. Abrams', 2839169916),
 ('Michael Bay', 2760938960),
 ('James Cameron', 2548546718),
 ('Francis Lawrence', 2476979588),
 ('Pierre Coffin', 2452006832),
 ('Steven Spielberg', 2449700791),
 ('Joss Whedon', 2424593677),
 ('Gore Verbinski', 2271362290),
 ('Sam Raimi', 2254066354),
 ('Lee Unkrich', 2081614145),
 ('Ridley Scott', 2044035909),
 ('Andrew Adamson', 1957706346),
 ('Chris Columbus', 1906968952),
 ('Carlos Saldanha', 1882719105),
 ('Tim Burton', 1801663457),
 ('Eric Darnell', 1755054393),
 ('Sam Mendes', 1710352791),
 ('Tom McGrath', 1705388064),
 ('Pete Docter', 1682867609),
 ('Chris Renaud', 1648116186),
 ('James Wan', 1620441367),
 ('Brad Bird', 1581913958),
 ('Conrad Vernon', 1578269902),
 ('Shawn Levy', 1515787063),
 ('Justin Lin', 1472947074),
 ('Steven Soderbergh', 1450928588),
 ('Ron Howard', 1385437233),
 ('Bill Condon', 1376664544),
 ('Colin Trevorrow', 1363528810),
 

# 14. Какой режисер снял больше всего фильмов в стиле Action?

In [52]:
answers['14'] = '3. Robert Rodriguez'

In [53]:
(
    data[['director_set', 'genre_set']]
    .apply(
        lambda x: Counter(
            {name: ('Action' in x.genre_set) for name in x.director_set }
        ),
        axis='columns'
    )
    .sum()
    .most_common()
)

[('Robert Rodriguez', 9),
 ('Michael Bay', 7),
 ('Paul W.S. Anderson', 7),
 ('Antoine Fuqua', 6),
 ('Ridley Scott', 6),
 ('Brett Ratner', 5),
 ('Quentin Tarantino', 5),
 ('Zack Snyder', 5),
 ('Roland Emmerich', 5),
 ('Andrzej Bartkowiak', 5),
 ('Louis Leterrier', 5),
 ('Tony Scott', 5),
 ('Paul Greengrass', 5),
 ('Peter Jackson', 5),
 ('Lee Tamahori', 5),
 ('Gore Verbinski', 5),
 ('Rob Cohen', 5),
 ('Peter Berg', 5),
 ('J.J. Abrams', 4),
 ('Lana Wachowski', 4),
 ('Lilly Wachowski', 4),
 ('Olivier Megaton', 4),
 ('Guy Ritchie', 4),
 ('Bryan Singer', 4),
 ('Tim Story', 4),
 ('Renny Harlin', 4),
 ('Brian Taylor', 4),
 ('Mark Neveldine', 4),
 ('Dominic Sena', 4),
 ('Justin Lin', 4),
 ('Christopher Nolan', 4),
 ('Simon West', 4),
 ('John Moore', 4),
 ('Steven Spielberg', 4),
 ('Martin Campbell', 4),
 ('John Singleton', 4),
 ('Len Wiseman', 4),
 ('Brad Bird', 3),
 ('Matthew Vaughn', 3),
 ('Neill Blomkamp', 3),
 ('Jaume Collet-Serra', 3),
 ('Breck Eisner', 3),
 ('Pierre Morel', 3),
 ('David A

# 15. Фильмы с каким актером принесли самые высокие кассовые сборы в 2012 году? 

In [54]:
answers['15'] = '3. Chris Hemsworth'

In [55]:
(
    data[data.release_year == 2012][['cast_set', 'profit']]
    .apply(
        lambda x: Counter(
            {name: x.profit for name in x.cast_set }
        ),
        axis='columns'
    )
    .sum()
    .most_common()
)

[('Chris Hemsworth', 1542450773),
 ('Denis Leary', 1319460639),
 ('Scarlett Johansson', 1299557910),
 ('Robert Downey Jr.', 1299557910),
 ('Mark Ruffalo', 1299557910),
 ('Chris Evans', 1299557910),
 ('Anne Hathaway', 1211851057),
 ('Sacha Baron Cohen', 1097110577),
 ('Ralph Fiennes', 1059561013),
 ('Seann William Scott', 967234366),
 ('Kristen Stewart', 919384318),
 ('Naomie Harris', 908561013),
 ('Judi Dench', 908561013),
 ('Daniel Craig', 908561013),
 ('Javier Bardem', 908561013),
 ('Josh Hutcherson', 872710235),
 ('Tom Hardy', 858717867),
 ('Gary Oldman', 831041287),
 ('Michael Caine', 831041287),
 ('Christian Bale', 831041287),
 ('Jennifer Lawrence', 800949406),
 ('Chris Wedge', 782244782),
 ('Ray Romano', 782244782),
 ('John Leguizamo', 779138503),
 ('Ian McKellen', 767003568),
 ('Andy Serkis', 767003568),
 ('Cate Blanchett', 767003568),
 ('Martin Freeman', 767003568),
 ('Richard Armitage', 767003568),
 ('Emma Thompson', 753009983),
 ('Elizabeth Reaser', 709000000),
 ('Peter Facin

# 16. Какой актер снялся в большем количестве высокобюджетных фильмов?

In [56]:
answers['16'] = '3. Matt Damon'

In [57]:
(
    data[data.budget > data.budget.mean()]
    .cast_set
    .apply(Counter)
    .sum()
    .most_common()
)

[('Matt Damon', 18),
 ('Adam Sandler', 17),
 ('Angelina Jolie', 16),
 ('Tom Cruise', 15),
 ('Samuel L. Jackson', 15),
 ('Eddie Murphy', 15),
 ('Mark Wahlberg', 14),
 ('Hugh Jackman', 14),
 ('Ben Stiller', 14),
 ('Jamie Foxx', 14),
 ('Russell Crowe', 14),
 ('Johnny Depp', 13),
 ('Jude Law', 13),
 ('Bruce Willis', 13),
 ('Will Smith', 13),
 ('Dwayne Johnson', 12),
 ('Ian McKellen', 12),
 ('Brad Pitt', 12),
 ('Owen Wilson', 12),
 ('Cameron Diaz', 12),
 ('Nicolas Cage', 12),
 ('Robert De Niro', 12),
 ('Leonardo DiCaprio', 11),
 ('Daniel Craig', 11),
 ('Robert Downey Jr.', 11),
 ('Steve Buscemi', 11),
 ('Vin Diesel', 10),
 ('Mark Ruffalo', 10),
 ('Jack Black', 10),
 ('Denzel Washington', 10),
 ('Emma Watson', 10),
 ('Gary Oldman', 10),
 ('Tom Hanks', 10),
 ('Orlando Bloom', 10),
 ('Ralph Fiennes', 9),
 ('Cate Blanchett', 9),
 ('Michael Caine', 9),
 ('Paul Bettany', 9),
 ('Ewan McGregor', 9),
 ('Brendan Gleeson', 9),
 ('Shia LaBeouf', 9),
 ('Nicole Kidman', 9),
 ('Colin Farrell', 9),
 ('Rach

# 17. В фильмах какого жанра больше всего снимался Nicolas Cage? 

In [58]:
answers['17'] = '2. Action'

In [59]:
(
    data[
        data.cast_set.apply(lambda x: 'Nicolas Cage' in x)
    ]
    .genre_set
    .apply(Counter)
    .sum()
    .most_common()
)

[('Action', 17),
 ('Thriller', 15),
 ('Drama', 12),
 ('Crime', 10),
 ('Fantasy', 8),
 ('Adventure', 7),
 ('Comedy', 6),
 ('Science Fiction', 4),
 ('Mystery', 3),
 ('Animation', 3),
 ('Family', 3),
 ('History', 2),
 ('War', 1),
 ('Horror', 1),
 ('Romance', 1)]

# 18. Самый убыточный фильм от Paramount Pictures

In [60]:
answers['18'] = '1. K-19: The Widowmaker (tt0267626)'

In [61]:
(
    data[
        data.production_companies.str.contains(r'Paramount\s*Pictures')
    ]
    [['neat_title', 'profit']]
    .sort_values('profit')
    .neat_title
    .to_list()
)

['K-19: The Widowmaker (tt0267626)',
 'Timeline (tt0300556)',
 'Next (tt0435705)',
 'Alfie (tt0375173)',
 'Twisted (tt0315297)',
 'Domestic Disturbance (tt0249478)',
 'The Love Guru (tt0811138)',
 'A Thousand Words (tt0763831)',
 'The Fighter (tt0964517)',
 'Abandon (tt0267248)',
 'Suspect Zero (tt0324127)',
 'Serving Sara (tt0261289)',
 'Sky Captain and the World of Tomorrow (tt0346156)',
 'Sahara (tt0318649)',
 'Ã†on Flux (tt0402022)',
 'Jack Ryan: Shadow Recruit (tt1205537)',
 'The Weather Man (tt0384680)',
 'Last Holiday (tt0408985)',
 'The Four Feathers (tt0240510)',
 'Elizabethtown (tt0368709)',
 'Fun Size (tt1663143)',
 'The Score (tt0227445)',
 'Bad News Bears (tt0408524)',
 "Get Rich or Die Tryin' (tt0430308)",
 'Star Trek: Nemesis (tt0253754)',
 'Hardball (tt0180734)',
 'Young Adult (tt1625346)',
 'Rules of Engagement (tt0160797)',
 'The Stepford Wives (tt0327162)',
 'Clockstoppers (tt0157472)',
 'The Gambler (tt2039393)',
 'The Core (tt0298814)',
 'Extremely Loud & Incredibl

# 19. Какой год стал самым успешным по суммарным кассовым сборам?

In [62]:
answers['19'] = '5. 2015'

In [63]:
data.groupby('release_year').profit.sum().sort_values(ascending=False)

release_year
2015    18668572378
2014    16397812953
2012    16077001687
2013    15243179791
2011    14730241341
2010    13531204961
2009    13423744372
2008    11663881990
2007    11565911801
2004     9634180720
2003     9228823312
2002     9002361487
2005     8981925558
2006     8691077320
2001     7950614865
2000     6101399805
Name: profit, dtype: int64

# 20. Какой самый прибыльный год для студии Warner Bros?

In [64]:
answers['20'] = '1. 2014'

In [65]:
(
    data[
        data.production_companies.str.contains(r'Warner\s*Bros')
    ]
    .groupby('release_year')
    .profit
    .sum()
    .sort_values(ascending=False)
)

release_year
2014    2295464519
2007    2201675217
2008    2134595031
2010    1974712985
2011    1871393682
2003    1855493377
2009    1822454136
2013    1636453400
2004    1631933725
2005    1551980298
2001    1343545668
2012    1258020056
2002    1022709901
2015     870368348
2006     620170743
2000     452631386
Name: profit, dtype: int64

# 21. В каком месяце за все годы суммарно вышло больше всего фильмов?

In [66]:
answers['21'] = '4. Сентябрь'

In [67]:
(
    data
    .groupby(
        data.release_date.apply(lambda x: x.month)
    )
    .imdb_id
    .count()
    .sort_values(ascending=False)
)

release_date
9     227
12    190
10    186
8     161
3     156
4     149
6     147
11    146
7     142
5     140
2     135
1     110
Name: imdb_id, dtype: int64

ВАРИАНТ 2

In [68]:
Counter(
    data.release_month
).most_common()

[(9, 227),
 (12, 190),
 (10, 186),
 (8, 161),
 (3, 156),
 (4, 149),
 (6, 147),
 (11, 146),
 (7, 142),
 (5, 140),
 (2, 135),
 (1, 110)]

# 22. Сколько суммарно вышло фильмов летом? (за июнь, июль, август)

In [69]:
answers['22'] = '2. 450'

In [70]:
len(
    data
    .query('6 <= release_month <= 8')
)

450

# 23. Для какого режиссера зима – самое продуктивное время года? 

In [71]:
answers['23'] = '5. Peter Jackson'

In [72]:
(
    data[
        data.release_month.isin({12, 1, 2})
    ]
    .director_set
    .apply(Counter)
    .sum()
    .most_common()
)

[('Peter Jackson', 7),
 ('Clint Eastwood', 6),
 ('Steven Soderbergh', 6),
 ('Shawn Levy', 4),
 ('Nancy Meyers', 4),
 ('Martin Scorsese', 4),
 ('Adam Shankman', 4),
 ('Ridley Scott', 3),
 ('Rob Marshall', 3),
 ('Tim Burton', 3),
 ('Steve Carr', 3),
 ('Patrick Lussier', 3),
 ('Donald Petrie', 3),
 ('Marc Lawrence', 3),
 ('Lasse HallstrÃ¶m', 3),
 ('Edward Zwick', 3),
 ('Aaron Seltzer', 3),
 ('Jason Friedberg', 3),
 ('Peter Farrelly', 3),
 ('Steven Spielberg', 3),
 ('Wayne Wang', 3),
 ('Quentin Tarantino', 2),
 ('Adam McKay', 2),
 ('Michael Mann', 2),
 ('John Requa', 2),
 ('Glenn Ficarra', 2),
 ('Pierre Morel', 2),
 ('Wes Anderson', 2),
 ('Paul Thomas Anderson', 2),
 ('Jaume Collet-Serra', 2),
 ('George Clooney', 2),
 ('Shana Feste', 2),
 ('Ken Kwapis', 2),
 ('Henry Selick', 2),
 ('P.J. Hogan', 2),
 ('David S. Goyer', 2),
 ('Paul McGuigan', 2),
 ('Marcus Nispel', 2),
 ('Andrzej Bartkowiak', 2),
 ('Scott Cooper', 2),
 ('Allen Hughes', 2),
 ('Garry Marshall', 2),
 ('David O. Russell', 2),
 (

# 24. Какая студия дает самые длинные названия своим фильмам по количеству символов?

In [73]:
answers['24'] = '5. Four By Two Productions'

In [74]:
data2 = data.copy()
data2['company_list'] = data2.company_set.apply(list)
data2 = (
    data2
    .explode('company_list')
    .rename(columns={'company_list': 'company'})
    .copy()
)

data2['title_length'] = data2.original_title.apply(len)

(
    data2
    .groupby('company')
    .title_length
    .max()
    .sort_values(ascending=False)
    .to_dict()
)

{'Four By Two Productions': 83,
 'Twentieth Century Fox Film Corporation': 83,
 'Walden Media': 62,
 'Walt Disney': 62,
 'Jim Henson Company, The': 59,
 '21 Laps Entertainment': 59,
 'Walt Disney Pictures': 59,
 'Warner Bros.': 58,
 'Plan B Entertainment': 58,
 'Virtual Studios': 58,
 'Alberta Film Entertainment': 58,
 'Scott Free Productions': 58,
 'Fox 2000 Pictures': 56,
 'Dune Entertainment': 56,
 'Jerry Bruckheimer Films': 54,
 '1492 Pictures': 50,
 'Lucasfilm': 50,
 'Paramount Pictures': 50,
 'Sunswept Entertainment': 50,
 'Ingenious Film Partners': 50,
 'WingNut Films': 49,
 'The Saul Zaentz Company': 49,
 'New Line Cinema': 49,
 'Miramax': 47,
 'Nickelodeon Movies': 47,
 'Universal Pictures': 47,
 'Dos Corazones': 47,
 'Kumar Mobiliengesellschaft mbH & Co. Projekt Nr. 2 KG': 47,
 'Samuel Goldwyn Films': 47,
 'Scott Rudin Productions': 47,
 'DreamWorks Pictures': 47,
 'Edward R. Pressman Film': 46,
 'Tim Burton Productions': 46,
 'Parkes+MacDonald Image Nation': 46,
 'Museum Can

# 25. Описание фильмов какой студии в среднем самые длинные по количеству слов?

In [75]:
answers['25'] = '3. Midnight Picture Show'

In [76]:
data2 = data.copy()
data2['company_list'] = data2.company_set.apply(list)
data2 = (
    data2
    .explode('company_list')
    .rename(columns={'company_list': 'company'})
    .copy()
)
data2['word_count'] = (
    data2
    .overview
    .str
    .replace(r'[,.!?/|\()\[\]~-]', r' ')
    .apply(lambda x: len(str(x).split()))
)

(
    data2
    .groupby('company')
    .word_count
    .mean()
    .sort_values(ascending=False)
    .to_dict()
)

{'Midnight Picture Show': 175.0,
 '98 MPH Productions': 167.0,
 'Room 9 Entertainment': 166.0,
 'Heineken Branded Entertainment': 161.0,
 'Brookwell-McNamara Entertainment': 159.0,
 'Lions Gate Family Entertainment': 155.0,
 'Crest Animation Productions': 155.0,
 'Art Pictures Studio': 148.0,
 'Sanctum Australia': 145.0,
 'Great Wight Productions/ Osford Films': 145.0,
 'Wayfare Entertainment': 145.0,
 'Starbucks Entertainment': 144.0,
 'Cinema Gypsy Productions': 144.0,
 'Sudden Storm Productions': 136.0,
 'Magical Elves Productions': 134.0,
 'Scooter Braun Films': 134.0,
 'Disney Double Dare You (DDY)': 132.0,
 'K. JAM Media': 131.0,
 'Silent Hill DCP Inc.': 126.0,
 'Konami': 126.0,
 'Radical Studios': 125.5,
 'Omega Entertainment': 120.0,
 'Pantheon Entertainment Corporation': 120.0,
 'Innocence Productions': 120.0,
 'Oceana Media Finance': 120.0,
 'David Ladd Films': 120.0,
 'O.N.C. Entertainment': 118.0,
 'Ex3 Productions': 118.0,
 'Crying Box Productions': 117.0,
 'Ten Thirteen P

# 26. Какие фильмы входят в 1 процент лучших по рейтингу? 
по vote_average

In [77]:
answers['26'] = '1. Inside Out, The Dark Knight, 12 Years a Slave'

In [78]:
(
    data[data.vote_average > data.vote_average.quantile(.99)]
    .neat_title
    .to_list()
)

['Inside Out (tt2096673)',
 'Room (tt3170832)',
 'Interstellar (tt0816692)',
 'Guardians of the Galaxy (tt2015381)',
 'The Imitation Game (tt2084970)',
 'Gone Girl (tt2267998)',
 'The Grand Budapest Hotel (tt2278388)',
 'Inception (tt1375666)',
 'The Dark Knight (tt0468569)',
 'The Pianist (tt0253474)',
 'The Lord of the Rings: The Return of the King (tt0167260)',
 'The Wolf of Wall Street (tt0993846)',
 '12 Years a Slave (tt2024544)',
 'Memento (tt0209144)']

# 27. Какие актеры чаще всего снимаются в одном фильме вместе?


In [79]:
answers['27'] = '5. Daniel Radcliffe & Rupert Grint'

Окей, для этого задания я не нашёл простого решения. Поэтому буду брутфорсить.

Вот основные действия по шагам:

### 27.1 Подготовить actors_and_movies_df

Это датафрейм где выписываются в плоском виде все отношения актёров и фильмов.

In [80]:
data2 = data.copy();
data2['cast_list'] = data2.cast_set.apply(list)

actors_and_movies_df = (
    data2
    .explode('cast_list')
    .rename(columns={'cast_list': 'actor'})
    [['actor', 'imdb_id']]
)
actors_and_movies_df

actor    imdb_id
0             Chris Pratt  tt0369610
0             Irrfan Khan  tt0369610
0       Vincent D'Onofrio  tt0369610
0     Bryce Dallas Howard  tt0369610
0           Nick Robinson  tt0369610
...                   ...        ...
1888        Nathan Bexton  tt0163676
1888           Susan Ward  tt0163676
1888       Matthew Settle  tt0163676
1888         Lori Heuring  tt0163676
1888          Tess Harper  tt0163676

[9437 rows x 2 columns]

### 27.2 Подготовить all_actor_list

Это - список вообще всех актёров в датасете.

In [81]:
all_actor_list = list(actors_and_movies_df.actor.unique())
pd.DataFrame(all_actor_list)

0
0             Chris Pratt
1             Irrfan Khan
2       Vincent D'Onofrio
3     Bryce Dallas Howard
4           Nick Robinson
...                   ...
3401        Nathan Bexton
3402           Susan Ward
3403       Matthew Settle
3404         Lori Heuring
3405          Tess Harper

[3406 rows x 1 columns]

Ого, 3 с половиной тысячи человек. Не мало.

### 27.3 Сгруппировать actors_and_movies_df по фильмам

In [82]:
actors_per_movie_g = actors_and_movies_df.groupby('imdb_id')

### 27.4 Подготовить actor_s_list

По сути - проходим по группам и из каждой вытягиваем связку в которой - список актёров, привязанные к данному фильму. Потом приводим эту связку к тому формату который кажется удобней - например мне сейчас это кажется *pandas.Series*.

Этот проход занимает немного времени, но у меня - не дольше 20 секунд. Можно подождать.

In [83]:
print('generating actor_s_list...')
actor_s_list = []

# Этот цикл будет выполняться дюжину или две секунд, поэтому мне нужно
# видеть прогресс чтобы оценить время которое занимает операция.
# Индикатор прогресса можно было реализовать по-разному - сделал в форме
# которая мне была нужна.
i_last_milestone = -1
i_milestone_increment = 50
i = 0
i_total = len(actors_per_movie_g)

for imdb_id, actor_df in actors_per_movie_g:
    
    i += 1
    i_current_milestone = int(i/i_milestone_increment)
    if i_current_milestone != i_last_milestone:
        print(f'milestone reached: group {i} / {i_total}')
        i_last_milestone = i_current_milestone
    
    actor_list = list(
        actor_df
        .actor
        .unique()
    )
    
    actor_s = pd.Series(index=actor_list, dtype=int) + 1
    
    actor_s_list.append(actor_s)
    
else:
    print(f'milestone reached: group {i} / {i_total}')
print('ok')
print()

generating actor_s_list...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1250 / 1889
milestone reached: group 1300 / 18

### 27.5 Подготовить result_counter_list

Эта операция скорее всего займёт несколько минут - но как только мы её завершим - задача будет уже почти решена.

Мы проходимся по списку всех актёров *all_actor_list* и с его точки зрения, проходимся по actor_s_list. Среди actor_s_list мы отбираем те фильмы в которых он участвовал. И мы используем *collections.Counter* чтобы начать считать всех коллег с котороми этот актёр разделяет фильм.

result_counter_list - это список, каждый элемент которого - *collections.Counter*, внутри которого перечисляются пары актёров которые - с точки зрения одного из участников этих пар - сотрудничали в наибольшем количестве фильмов по сравнению с их коллегами.

In [84]:
result_counter_list = []

for actor_count, actor in enumerate(all_actor_list):
    
    print(
        f'generating actor_to_actors_df for actor {actor} ' +
        f'{actor_count} / {len(all_actor_list)}...'
    )
    comrade_counter = Counter()
    best_comrades = Counter()
    
    # Этот цикл будет долго выполняться, поэтому мне нужно видеть
    # прогресс чтобы оценить время которое занимает операция. Индикатор
    # прогресса можно было реализовать по-разному - сделал в форме
    # которая мне была нужна.
    i_last_milestone = -1
    i_milestone_increment = 50
    i = 0
    i_total = len(actor_s_list)
    
    for actor_s in actor_s_list:
        
        i += 1
        i_current_milestone = int(i/i_milestone_increment)
        if i_current_milestone != i_last_milestone:
            print(f'milestone reached: group {i} / {i_total}')
            i_last_milestone = i_current_milestone
        
        if actor in actor_s.index:
            comrade_counter += Counter(actor_s.to_dict())
            
            # Если у нас актёр - Мел Гибсон, то мы не хотим в списке
            # товарищей считать его в каждой группе как отдельного
            # друга. Ведь тогда он будет гарантировано во всех группах -
            # а значит самый лучший друг! Поэтому - удалить Мела Гибсона
            # из списка товарищей.
            comrade_counter.pop(actor, None)
            
            # Для объектов Counter, после внесения изменений в словарь
            # надо не забывать дёргать пересчёт.
            comrade_counter.update()
            
    else:
        print(f'milestone reached: group {i} / {i_total}')
    
    best_comrades = Counter(
        pd.DataFrame(
            comrade_counter.most_common(),
            columns=['actor', 'common_count']
        )
        .query('common_count == common_count.max()')
        .apply(lambda x: Counter({x.actor: x.common_count}), axis='columns')
        .sum()
    )
    
    best_comrades = Counter({ actor+'|'+i: j for i, j in best_comrades.items()})
    
    result_counter_list.append(best_comrades)
    
    print('ok')
    print()


print('finished')

generating actor_to_actors_df for actor Chris Pratt 0 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1250 / 18

milestone reached: group 1550 / 1889
milestone reached: group 1600 / 1889
milestone reached: group 1650 / 1889
milestone reached: group 1700 / 1889
milestone reached: group 1750 / 1889
milestone reached: group 1800 / 1889
milestone reached: group 1850 / 1889
milestone reached: group 1889 / 1889
ok

generating actor_to_actors_df for actor Charlize Theron 8 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: grou

milestone reached: group 1500 / 1889
milestone reached: group 1550 / 1889
milestone reached: group 1600 / 1889
milestone reached: group 1650 / 1889
milestone reached: group 1700 / 1889
milestone reached: group 1750 / 1889
milestone reached: group 1800 / 1889
milestone reached: group 1850 / 1889
milestone reached: group 1889 / 1889
ok

generating actor_to_actors_df for actor Harrison Ford 15 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: grou

ok

generating actor_to_actors_df for actor Jason Statham 22 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 12

milestone reached: group 1700 / 1889
milestone reached: group 1750 / 1889
milestone reached: group 1800 / 1889
milestone reached: group 1850 / 1889
milestone reached: group 1889 / 1889
ok

generating actor_to_actors_df for actor Jai Courtney 30 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 100

...

milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1250 / 1889
milestone reached: group 1300 / 1889
milestone reached: group 1350 / 1889
milestone reached: group 1400 / 1889
milestone reached: group 1450 / 1889
milestone reached: group 1500 / 1889
milestone reached: group 1550 / 1889
milestone reached: group 1600 / 1889
milestone reached: group 1650 / 1889
milestone reached: group 1700 / 1889
milestone reached: group 1750 / 1889
milestone reached: group 1800 / 1889
milestone reached: group 1850 / 1889
milestone reached: group 1889 / 1889
ok

generating actor_to_actors_df for actor GÃ©rard Depardieu 3374 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone

ok

generating actor_to_actors_df for actor Lily Tomlin 3381 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 12

ok

generating actor_to_actors_df for actor Zoe McLellan 3389 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1

milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1250 / 1889
milestone reached: group 1300 / 1889
milestone reached: group 1350 / 1889
milestone reached: group 1400 / 1889
milestone reached: group 1450 / 1889
milestone reached: group 1500 / 1889
milestone reached: group 1550 / 1889
milestone reached: group 1600 / 1889
milestone reached: group 1650 / 1889
milestone reached: group 1700 / 1889
milestone reached: group 1750 / 1889
milestone reached: group 1800 / 1889
milestone reached: group 1850 / 1889
milestone reached: group 1889 / 1889
ok

generating actor_to_actors_df for actor Pamela Gidley 3397 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone re

ok

generating actor_to_actors_df for actor Lori Heuring 3404 / 3406...
milestone reached: group 1 / 1889
milestone reached: group 50 / 1889
milestone reached: group 100 / 1889
milestone reached: group 150 / 1889
milestone reached: group 200 / 1889
milestone reached: group 250 / 1889
milestone reached: group 300 / 1889
milestone reached: group 350 / 1889
milestone reached: group 400 / 1889
milestone reached: group 450 / 1889
milestone reached: group 500 / 1889
milestone reached: group 550 / 1889
milestone reached: group 600 / 1889
milestone reached: group 650 / 1889
milestone reached: group 700 / 1889
milestone reached: group 750 / 1889
milestone reached: group 800 / 1889
milestone reached: group 850 / 1889
milestone reached: group 900 / 1889
milestone reached: group 950 / 1889
milestone reached: group 1000 / 1889
milestone reached: group 1050 / 1889
milestone reached: group 1100 / 1889
milestone reached: group 1150 / 1889
milestone reached: group 1200 / 1889
milestone reached: group 1

### 27.6 Получить пары актёров которые работали в наибольшем количестве фильмов

Финишная прямая которая даёт нам ответ на наш вопрос.

In [85]:
collected = Counter()

for result_counter in result_counter_list:
    collected += result_counter

collected.most_common(10)

[('Daniel Radcliffe|Emma Watson', 8),
 ('Daniel Radcliffe|Rupert Grint', 8),
 ('Emma Watson|Daniel Radcliffe', 8),
 ('Emma Watson|Rupert Grint', 8),
 ('Rupert Grint|Daniel Radcliffe', 8),
 ('Rupert Grint|Emma Watson', 8),
 ('Helena Bonham Carter|Johnny Depp', 6),
 ('Johnny Depp|Helena Bonham Carter', 6),
 ('Owen Wilson|Ben Stiller', 6),
 ('Ben Stiller|Owen Wilson', 6)]

# Submission

In [86]:
# в конце можно посмотреть свои ответы к каждому вопросу
answers

{'1': '5. Pirates of the Caribbean: On Stranger Tides (tt1298650)',
 '2': '2. Gods and Generals (tt0279111)',
 '3': '3. Winnie the Pooh (tt1449283)',
 '4': '2. 110',
 '5': '1. 107',
 '6': '5. Avatar (tt0499549)',
 '7': '5. The Lone Ranger (tt1210819)',
 '8': '1. 1478',
 '9': '4. The Dark Knight (tt0468569)',
 '10': '5. The Lone Ranger (tt1210819)',
 '11': '3. Drama',
 '12': '1. Drama',
 '13': '5. Peter Jackson',
 '14': '3. Robert Rodriguez',
 '15': '3. Chris Hemsworth',
 '16': '3. Matt Damon',
 '17': '2. Action',
 '18': '1. K-19: The Widowmaker (tt0267626)',
 '19': '5. 2015',
 '20': '1. 2014',
 '21': '4. Сентябрь',
 '22': '2. 450',
 '23': '5. Peter Jackson',
 '24': '5. Four By Two Productions',
 '25': '3. Midnight Picture Show',
 '26': '1. Inside Out, The Dark Knight, 12 Years a Slave',
 '27': '5. Daniel Radcliffe & Rupert Grint'}

In [87]:
# и убедиться что ни чего не пропустил)
len(answers)

27